In [168]:
from model import Encoder, Decoder, Seq2Seq
from data_loader import *
import pandas as pd
import torch.optim.lr_scheduler as lr_scheduler
from torch import optim
import torch.nn.functional as F
import datetime
import pretty_midi
import glob
import librosa

In [169]:
import os
import matplotlib
import math
matplotlib.use('Agg')
# matplotlib.use("QtAgg")
import ffmpeg
#conda install -c conda-forge ffmpeg-python

import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation, writers
plt.rcParams['animation.ffmpeg_path'] = '/home/ilc/anaconda3/bin/ffmpeg'#'/usr/bin/ffmpeg'

import numpy as np
import subprocess as sp
from moviepy.video.io.VideoFileClip import VideoFileClip
from moviepy.audio.io.AudioFileClip import AudioFileClip

from midi2audio import FluidSynth

from torch.autograd import Variable 

In [ ]:
import gc
gc.collect()
torch.cuda.empty_cache()

KeyboardInterrupt: 

In [ ]:
dataset_name_path = f"./audio_list.txt" #f"./midi_list.txt"
dataloader = get_audio_dataloader(dataset_name_path, batch_size=128) #[20, 512, 128], [20, 512, 102]

val_dataset_name_path = f"./audio_list_eval.txt" #f"./midi_list_eval.txt"
val_dataloader = get_audio_val_dataloader(val_dataset_name_path, batch_size=128) #[20, 512, 128], [20, 512, 102]

learning_rate = 0.001#0.001

input_size_encoder = 28 #128 #129 #128
input_size_decoder = 102 #102 #24
output_size = 102#102 #24

# encoder_embedding_size = 300
# decoder_embedding_size = 300
enc_dropout = 0.5
dec_dropout = 0.
step = 0

device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
print(device)

self.piece_count:  105
dataset_len:  10500
val_dataset_len 5
cuda:0


In [ ]:
class LSTM1(nn.Module):
    def __init__(self, output_dim, input_size, hidden_size, num_layers, seq_length):
        super(LSTM1, self).__init__()
        self.output_dim = output_dim #number of classes
        self.num_layers = num_layers #number of layers
        self.input_size = input_size #input size
        self.hidden_size = hidden_size #hidden state
        self.seq_length = seq_length #sequence length

        self.lstm = nn.LSTM(input_size=input_size, hidden_size=hidden_size,
                          num_layers=num_layers, batch_first=True) #lstm
        self.fc_1 =  nn.Linear(hidden_size, output_dim) #fully connected to determine output dim

        self.relu = nn.ReLU()

    def forward(self,x):
        # h0, c0 no time information
        h_0 = Variable(torch.zeros(self.num_layers, x.size(0), self.hidden_size)).to(device) #hidden state
        c_0 = Variable(torch.zeros(self.num_layers, x.size(0), self.hidden_size)).to(device) #internal state
        # Propagate input through LSTM
        # x is MIDI => [44, 512, 128]

        # hn is final state, run over the sequence length
        output, (hn, cn) = self.lstm(x, (h_0, c_0)) #lstm with input, hidden, and internal state
        # hn = hn.view(-1, self.hidden_size) #reshaping the data for Dense layer next
        # print("output.shape", output.shape)
        # print("hn.shape", hn.shape)
        # out = self.relu(hn)
        out = self.fc_1(output) #final
        return out
 

In [ ]:
# Define the model architecture
input_size = 28 #number of features
hidden_size = 256 #number of features in hidden state
num_layers = 1 #number of stacked lstm layers
seq_len = 512
output_dim = 102 #number of output classes

# model = LSTM(vocab_size, embedding_dim, hidden_dim, num_layers, dropout_rate, tie_weights).to(device)
# model = LSTM(embedding_dim, hidden_dim, num_layers, dropout_rate, tie_weights).to(device)
model = LSTM1(output_dim, input_size, hidden_size, num_layers, seq_len).to(device) #our lstm class
model.train()

optimizer = optim.Adam(model.parameters(), lr=learning_rate)
# scheduler = optim.lr_scheduler.ReduceLROnPlateau(optimizer, mode='min', factor=0.1, patience=2)

num_epochs = 500 #10
avg_loss_list = []
all_loss_list = []
val_loss_per_epoch_list = []

In [ ]:
def customized_mse_loss(output, target, prev_output, midi_array):
    # target = target.transpose(0, 1)
    # print("output", output)
    # print(output.shape) #torch.Size([20, 513, 102])
    # print(target.shape) #torch.Size([20, 513, 102])
    mse_loss = F.mse_loss(output, target)
    # print("mse_loss:", mse_loss)

    var_diff = torch.var(torch.squeeze(output), dim=1, keepdim=True)
    mean_diff = torch.mean(var_diff)
    
    # Condition 1: Penalize if output is similar to previous output
    if mean_diff < 1e-4: #threshold
        #output [512, 1, 102] => [102] <-> [102] <-> [102] <-> ... <-> [102]
        mse_loss *= 1000

    # Condition 2: Stop movement if input is all zeros
    # midi_transpose = midi_array.transpose(0, 1)
    # midi_sum_row = torch.sum(midi_transpose, dim=-1)
    # mask = midi_sum_row == 0
    # mask = mask.unsqueeze(-1)
    # mask = mask.to(device)
    # # according to recorded index, make a mask [0, 1, 1, 0, ..., 0], true part will be omit(set value to 0).
    # # before compute mse, use mask first to tensor, then caculate MES loss
    # masked_output = output.masked_fill(mask, 0) #inplace function
    # masked_target = target.masked_fill(mask, 0)
    # mse_loss += F.mse_loss(masked_output, masked_target) * 100 #output 和 previous output 不像的話，增大 loss

    # Condition 3: Penalize if right-hand movement is too different between outputs
    # if output.shape[-1] == 21:  # Assumes hand joints are the last 21 dimensions
    #     rh_indices = [i for i in range(12, 21)]  # Right-hand joint indices
    #     rh_output = output[..., rh_indices]
    #     rh_prev_output = prev_output[..., rh_indices]
    #     rh_loss = nn.functional.mse_loss(rh_output, rh_prev_output)
    #     if rh_loss > 0.1:
    #         mse_loss *= 1000

    return mse_loss

In [ ]:
def evaluate_lstm(model, val_dataloader):
    model.eval()
    print('Validation')
    valid_running_loss = 0.0
    counter = 0
    # previous_output = torch.zeros(512, 102).to(device)
    with torch.no_grad():
        for i, (inputs, targets) in enumerate(val_dataloader): #tqdm(enumerate(val_dataloader), total=len(val_dataloader))
            counter += 1

            inputs = inputs.to(device).float()
            targets = targets.to(device).float()
            print("inputs.shape:", inputs.shape)
            print("targets.shape:", targets.shape)
            outputs = model(inputs)
            print("outputs.shape:", outputs.shape)

            loss =  F.mse_loss(outputs, targets)
            valid_running_loss += loss.cpu().item()
            # previous_output = outputs

    epoch_val_loss = valid_running_loss / counter
    return epoch_val_loss

In [ ]:
def evaluate_l1(model, val_dataloader):
    model.eval()
    print('Validation L1')
    valid_running_loss = 0.0
    counter = 0
    # previous_output = torch.zeros(512, 102).to(device)
    with torch.no_grad():
        for i, (inputs, targets) in enumerate(val_dataloader): #tqdm(enumerate(val_dataloader), total=len(val_dataloader))
            counter += 1

            inputs = inputs.to(device).float()
            targets = targets.to(device).float()
            print("inputs.shape:", inputs.shape)
            print("targets.shape:", targets.shape)
            outputs = model(inputs)
            print("outputs.shape:", outputs.shape)

            loss =  F.l1_loss(outputs, targets)
            valid_running_loss += loss.cpu().item()
            # previous_output = outputs

    epoch_val_loss = valid_running_loss / counter
    return epoch_val_loss

In [ ]:
# train the model
for epoch in range(num_epochs):
    # previous_output = torch.zeros(1, 512, 102).to(device)
    losses = []
    for i, (audio_batch, motion_batch) in enumerate(dataloader):
        model.train()
        
        audio_batch = audio_batch.to(device).float()
        motion_batch = motion_batch.to(device).float()
        print("audio_batch", audio_batch.shape)
        print("motion_batch", motion_batch.shape)

        optimizer.zero_grad()
        output = model(audio_batch) #audio_batch
        print("output.shape", output.shape)

        # motion_ground_truth_padding = F.pad(motion_batch, (0,0,0,1), value = 1) #<eot>
        
        # loss =  F.mse_loss(output, motion_ground_truth_padding)
        loss =  F.mse_loss(output, motion_batch)
        # loss = customized_mse_loss(output, motion_ground_truth_padding, previous_output, midi_batch)
        # loss = customized_mse_loss(output, motion_batch, previous_output, midi_batch)

        # losses 累計lose
        losses.append(loss.cpu().item())
        all_loss_list.append(loss.cpu().item())
        loss.backward()

        optimizer.step()
        mean_loss = sum(losses)/len(losses)

        print(f"Epoch {epoch}, batch {i}: loss = {loss.cpu().item():.6f}")

        # scheduler.step(1)
        # previous_output = output

        loc_dt = datetime.datetime.today()
        loc_dt_format = loc_dt.strftime("%Y-%m-%d_%H-%M-%S")

    val_loss = evaluate_lstm(model, val_dataloader) #CUDA out of memory
    val_loss_per_epoch_list.append(val_loss)
    print(f"Epoch {epoch}: val_loss = {val_loss:.6f}")
    # save_best_model(
    #         val_loss, epoch, model, optimizer, loss, loc_dt_format, mean_loss
    #     )
    avg_loss_list.append(mean_loss)
    loc_dt = datetime.datetime.today()
    loc_dt_format = loc_dt.strftime("%Y-%m-%d_%H-%M-%S")
    if (epoch+1)%100 == 0:
        torch.save({
            'epoch':epoch,
            'model_state_dict':model.state_dict(),
            'optimizer_state_dict':optimizer.state_dict(),
            'loss':loss
        }, "./model_save/[audio]LSTM_save_epoch_" + str(epoch)+ "_"+ str(loc_dt_format) + "_avg_loss_" + str(mean_loss) +".tar")

audio_batch torch.Size([128, 512, 28])
motion_batch torch.Size([128, 512, 102])
output.shape torch.Size([128, 512, 102])
Epoch 0, batch 0: loss = 0.274931


audio_batch torch.Size([128, 512, 28])
motion_batch torch.Size([128, 512, 102])
output.shape torch.Size([128, 512, 102])
Epoch 0, batch 1: loss = 0.213912
audio_batch torch.Size([128, 512, 28])
motion_batch torch.Size([128, 512, 102])
output.shape torch.Size([128, 512, 102])
Epoch 0, batch 2: loss = 0.164333
audio_batch torch.Size([128, 512, 28])
motion_batch torch.Size([128, 512, 102])
output.shape torch.Size([128, 512, 102])
Epoch 0, batch 3: loss = 0.123117
audio_batch torch.Size([128, 512, 28])
motion_batch torch.Size([128, 512, 102])
output.shape torch.Size([128, 512, 102])
Epoch 0, batch 4: loss = 0.092826
audio_batch torch.Size([128, 512, 28])
motion_batch torch.Size([128, 512, 102])
output.shape torch.Size([128, 512, 102])
Epoch 0, batch 5: loss = 0.067234
audio_batch torch.Size([128, 512, 28])
motion_batch torch.Size([128, 512, 102])
output.shape torch.Size([128, 512, 102])
Epoch 0, batch 6: loss = 0.049657
audio_batch torch.Size([128, 512, 28])
motion_batch torch.Size([128, 5

In [ ]:
print(loc_dt_format)
print(avg_loss_list)

2023-07-17_19-47-15
[0.01734088372764548, 0.0018215557330299214, 0.0016358623180134468, 0.0015638764381004744, 0.0015008346547922455, 0.0014523246917447232, 0.0014237387888470147, 0.001384706853563527, 0.001368055438499404, 0.0013538898987112094, 0.0013553513121420898, 0.0013299642035356127, 0.0013154898321323365, 0.0013101533706109207, 0.0012888887754069216, 0.0013005626387894154, 0.0013141488286116756, 0.0012749530001913748, 0.001266103124257222, 0.0012887634213520102, 0.001295755865579718, 0.0012620415760159313, 0.0012632854176258825, 0.0012768469736855253, 0.0012511096443105713, 0.0012591080655938532, 0.0012360893579828273, 0.001235122966344457, 0.0012489542482892074, 0.0012173657025019806, 0.0012574794965919602, 0.0011943382875859198, 0.0011911040560499463, 0.0011809342863397247, 0.0012139998031331293, 0.0011685339366478554, 0.0011693491721076958, 0.001179126801014126, 0.0011584601660977196, 0.0011553234976144082, 0.0011451423942414392, 0.001153538185901132, 0.0011377609748651374,

In [ ]:
print(val_loss_per_epoch_list)

[0.0021862098947167397, 0.001951503800228238, 0.001860921736806631, 0.0018467503832653165, 0.0017326343804597855, 0.0017707014922052622, 0.0017748861573636532, 0.0016861935146152973, 0.0016777069540694356, 0.001864363788627088, 0.0016834520502015948, 0.001643738360144198, 0.0017090578330680728, 0.0016063435468822718, 0.001672019949182868, 0.0018878881819546223, 0.0016095840837806463, 0.0016077838372439146, 0.001684627728536725, 0.0019736888352781534, 0.0017235541017726064, 0.0016266177408397198, 0.0017553301295265555, 0.0016566679114475846, 0.0017718407325446606, 0.001708784606307745, 0.0017192444065585732, 0.002129332162439823, 0.0016840349417179823, 0.0019392046378925443, 0.0017062672413885593, 0.0016921079950407147, 0.0017294678837060928, 0.0020255136769264936, 0.001636227942071855, 0.0017381665529683232, 0.0018009473569691181, 0.001757259713485837, 0.0018553049303591251, 0.0017239091685041785, 0.001786253647878766, 0.0016426661750301719, 0.001725288457237184, 0.0017217228887602687,

In [ ]:
# def lr_lambda(epoch):
#     # LR to be 0.1 * (1/1+0.01*epoch)
#     base_lr = 0.1
#     factor = 0.01
#     return base_lr/(1+factor*epoch)

In [ ]:
# scheduler = lr_scheduler.LinearLR(optimizer, start_factor=1.0, end_factor=0.3, total_iters=10)
# scheduler = lr_scheduler.LambdaLR(optimizer, lr_lambda)

In [ ]:
plt.cla()
plt.clf()

In [ ]:
print(len(avg_loss_list))
avg_loss_list_dataframe = pd.DataFrame(avg_loss_list)

500


In [ ]:
avg_loss_list_dataframe

0
0    0.017341
1    0.001822
2    0.001636
3    0.001564
4    0.001501
..        ...
495  0.000659
496  0.000641
497  0.000658
498  0.000783
499  0.000785

[500 rows x 1 columns]

In [ ]:
plt.plot(np.array(avg_loss_list_dataframe.index), np.array(avg_loss_list_dataframe[0]))
plt.savefig("avg_loss_training.jpg")
plt.show()

In [ ]:
plt.cla()
plt.clf()

In [ ]:
loss_list_dataframe = pd.DataFrame(all_loss_list)

In [ ]:
plt.plot(np.array(loss_list_dataframe.index), np.array(loss_list_dataframe[0]))
plt.savefig("training_loss.jpg")
plt.show()

In [ ]:
plt.cla()
plt.clf()

In [ ]:
val_loss_per_epoch_list_dataframe = pd.DataFrame(val_loss_per_epoch_list)

In [ ]:
plt.plot(np.array(val_loss_per_epoch_list_dataframe.index), np.array(val_loss_per_epoch_list_dataframe[0]))
plt.savefig("training_val_loss.jpg")
plt.show()

In [ ]:
def predict(model, input, device):
    model.eval()
    with torch.no_grad():
        input = torch.as_tensor(input).to(torch.float32).to(device)
        # print(target.shape)
        # target = torch.as_tensor(target).to(torch.float32).to(device)
        # TODO: target should be <sos>, should not random
        outputs = model(input)
        return outputs.cpu().numpy()

In [ ]:
def audio_preprocess(audio_path, specific_fps):
    n_fft = 4096
    hop = int(44000/specific_fps) #1102.5 -> 40fps #882 -> 50fps
    y, sr = librosa.load(audio_path, sr=44000) #44000 for divide 40
    mfcc = librosa.feature.mfcc(y=y, sr=sr, n_fft=n_fft, hop_length=hop, n_mfcc=13)
    y = np.where(y == 0, 1e-10, y)
    energy = np.log(librosa.feature.rms(y=y, frame_length=n_fft, hop_length=hop, center=True))
    mfcc_energy = np.vstack((mfcc, energy))
    mfcc_delta = librosa.feature.delta(mfcc_energy)
    aud = np.vstack((mfcc_energy, mfcc_delta)).T
    
    print("hop:", hop)
    print("aud:", aud.shape)
    return aud

In [ ]:
test_datapath = "./BWV1001/"
change_fps = 40
test_audio_path_list = glob.glob(test_datapath + "*.wav")
test_data_list = []
test_music_list = []
for test_audio in test_audio_path_list:
    str_name = test_audio
    print("str_name:", str_name)
    filename = str_name.split('/')[2]
    filecode = filename.split('.')[0]
    print("filecode: ",filecode)
    test_music_list.append(filecode)
    
    print(test_audio)
    # read_piano_roll = read_midi(test_midi, change_fps)
    read_audio = audio_preprocess(test_audio, change_fps)
    # read_audio_transpose = read_audio
    print(read_audio.shape)
    test_audio_len = read_audio.shape[0]
    test_data_list.append(read_audio)

str_name: ./BWV1001/vs1-1ada.wav
filecode:  vs1-1ada
./BWV1001/vs1-1ada.wav


hop: 1100
aud: (8172, 28)
(8172, 28)
str_name: ./BWV1001/vs1-3sic.wav
filecode:  vs1-3sic
./BWV1001/vs1-3sic.wav
hop: 1100
aud: (6989, 28)
(6989, 28)
str_name: ./BWV1001/vs1-2fug.wav
filecode:  vs1-2fug
./BWV1001/vs1-2fug.wav
hop: 1100
aud: (11534, 28)
(11534, 28)
str_name: ./BWV1001/vs1-4prs.wav
filecode:  vs1-4prs
./BWV1001/vs1-4prs.wav
hop: 1100
aud: (7898, 28)
(7898, 28)


In [ ]:
def column(matrix, i):
    return [row[i] for row in matrix]

def test_render_animation(fps, output, azim, prediction, ground_truth=None):
    prediction_array = np.asarray(prediction)
    print(prediction_array.size)
    limit = len(prediction_array)
    print("limit", limit)
    size = 6#6
    fps = 40

    # Skeleton layout
    parents = [[0, 1], [1, 3], [3, 2], [0, 2],#head
                [8, 6], [6, 13], [13, 4], [4, 8],#shoulder
                [6, 4], [4, 5], [5, 7], [7, 6],#Upper torso
                [8, 18], [8, 20], [13, 21], [13, 19],
                [5, 20], [5, 21], [7, 18], [7, 19],
                [18, 19], [19, 21], [21, 20], [20, 18], #waist
                [18, 22], [20, 22], [22, 23], [22, 25], [23, 25], [24,23], [24, 25],  #right lag
                [21, 26], [19, 26], [26, 27], [26, 29], [27, 29], [28, 27], [28, 29], #left lag
                [8, 9], [9, 11], [9, 10], [10, 11], [10, 12], [9, 12], [11, 12], #right hand
                [13, 14], [14, 16], [14, 15], [16, 15], [14, 17], [16, 17], [15, 17], #left hand
                [31, 33], [30, 32], [30, 31], [32, 33], [31, 32], [30, 33] #instrument
                        ]
    # joints_right = [1, 2, 12, 13, 14]

    prediction_array[:, :, 2] += 0.1 #[:, :, 2]
    if ground_truth is not None:
        ground_truth[:, :, 2] += 0.1
        poses = {'Prediction': prediction_array,
                 'Ground_truth': ground_truth}
    else:
        poses = {'Prediction': prediction_array}
    

    fig = plt.figure()#(figsize=(size*len(poses), size))
    # ax_3d = []
    # lines_3d = []
    radius = 1#14 #3.7#
    # print(poses)
    for index, (title, data) in enumerate(poses.items()):
        ax = fig.add_subplot(1, len(poses), index + 1, projection='3d')
        ax.clear()
        print(data)
        ims = [] #每一 frame 都存
        for frame_index, each_frame in enumerate(data):
            # print("each_frame")
            # print(each_frame)
            ax.view_init(elev=15., azim=azim)
            ax.set_xlim3d([-radius/2, radius/2])
            ax.set_zlim3d([0, radius])
            ax.set_ylim3d([-radius/2, radius/2])
            ax.set_aspect('auto') #ax.set_aspect('equal')

            # print(title)
            points = ax.scatter(column(each_frame[:30], 0), column(each_frame[:30], 1), column(each_frame[:30], 2), cmap='jet', marker='o', label='body joint', color = 'black')
            points_2 = ax.scatter(column(each_frame[30:32], 0), column(each_frame[30:32], 1), column(each_frame[30:32], 2), cmap='jet', marker='o', label='body joint', color = 'blue')
            points_3 = ax.scatter(column(each_frame[32:34], 0), column(each_frame[32:34], 1), column(each_frame[32:34], 2), cmap='jet', marker='o', label='body joint', color = 'red')
            
            # ax.scatter(column(each_frame, 0), column(each_frame, 1), column(each_frame, 2), cmap='jet', marker='o', label='body joint')
            # ax.legend()
            # print("+++")
            
            parents = [[0, 1], [1, 3], [3, 2], [0, 2],#head
                        [8, 6], [6, 13], [13, 4], [4, 8],#shoulder
                        [6, 4], [4, 5], [5, 7], [7, 6],#Upper torso
                        [8, 18], [8, 20], [13, 21], [13, 19],
                        [5, 20], [5, 21], [7, 18], [7, 19],
                        [18, 19], [19, 21], [21, 20], [20, 18], #waist
                        [18, 22], [20, 22], [22, 23], [22, 25], [23, 25], [24,23], [24, 25],  #right lag
                        [21, 26], [19, 26], [26, 27], [26, 29], [27, 29], [28, 27], [28, 29], #left lag
                        [8, 9], [9, 11], [9, 10], [10, 11], [10, 12], [9, 12], [11, 12], #right hand
                        [13, 14], [14, 16], [14, 15], [16, 15], [14, 17], [16, 17], [15, 17], #left hand
                        [30, 31], [32, 33],  #instrument
                        # [31, 33], [30, 32], [30, 31], [32, 33], [31, 32], [30, 33] #instrument
                        ]
            lines = []
            # draw line
            
            # lines = [ax.plot([each_frame[vs][0], each_frame[ve][0]],
            #                  [each_frame[vs][1], each_frame[ve][1]],
            #                  [each_frame[vs][2], each_frame[ve][2]]) for (vs, ve) in parents]
            line_num = len(parents)
            for idx, each_line in enumerate(parents):
                vec_start = each_frame[each_line[0]]
                vec_end = each_frame[each_line[1]]
                # print(vec_start)
                # print(vec_end)
                line_color = "black"
                if idx == line_num-2:
                    line_color = "blue"
                if idx == line_num-1:
                    line_color = "red"
                # ax.plot([vec_start[0], vec_end[0]], [vec_start[1], vec_end[1]], [vec_start[2], vec_end[2]])
                
                temp, = ax.plot([vec_start[0], vec_end[0]], [vec_start[1], vec_end[1]], [vec_start[2], vec_end[2]], color=line_color)
                lines.append(temp)

            # ax.figure.savefig('./test_pic/pic' + str(frame_index) + '.png', dpi=100, bbox_inches = 'tight')

            # ims.append([points])
            # image_frame = [points].extend(lines)
            ims.append([points]+[points_2]+[points_3]+lines) #TODO: try extend

            # plt.cla()
            # print("+++")

    anim = matplotlib.animation.ArtistAnimation(fig, ims, interval=1000/fps)

    if output.endswith('.mp4'):
        FFwriter = matplotlib.animation.FFMpegWriter(fps=fps, extra_args=['-vcodec', 'libx264'])
        anim.save(output, writer=FFwriter)
    elif output.endswith('.gif'):
        anim.save(output, fps=fps, dpi=100, writer='imagemagick')
    else:
        raise ValueError('Unsupported output format (only .mp4 and .gif are supported)')

In [ ]:
def plot(audio_path, plot_path, prediction, sample_time, fps, name=""): #audio_path, plot_path, 
    # render_animation(fps, output='new_temp.mp4', azim=75, prediction=prediction)
    test_render_animation(fps, output='new_temp_' + name + '.mp4', azim=75, prediction=prediction)

    # # #merge with wav
    input_video = ffmpeg.input('new_temp_' + name + '.mp4')
    fluid_syn = FluidSynth()
    fluid_syn.midi_to_audio(audio_path, './output' + name + '.wav')
    input_audio = ffmpeg.input('./output' + name + '.wav')
    # output = ffmpeg.output(video, audio, plot_path, vcodec='copy', acodec='aac', strict='experimental')
    ffmpeg.concat(input_video, input_audio, v=1, a=1).output(plot_path).run()
    # os.remove('new_temp_' + name + '.mp4')

In [ ]:
model.eval()

full_prediction = pd.DataFrame()
num_count = 0
# read midi
# test_dataloader = get_dataloader(test_datapath, batch_size=1)
for test_batch in test_data_list:
    with torch.no_grad():
        # first_target = torch.zeros(test_batch.shape[0],112)
        # print(first_target.shape)
        test_input = test_batch[None, :]
        # test_target = first_target[None, :]
        print("test_input", test_input.shape)
        # print("test_target", test_target.shape)
        prediction = predict(model, test_input, device)
        
        # print(prediction.shape)
        
        prediction  = prediction[:, :, :102]
        print("prediction.shape", prediction.shape)
        
        # full_prediction.append(prediction)
        full_prediction = pd.DataFrame(prediction[0])
        print("full_prediction", full_prediction.shape)
        
        # prev_prediction = prediction[0][:-1][None, :]
        # print(prev_prediction.shape)
        
        Row_list_prediction =[]
        
        filecode = test_music_list[num_count]
    
        # Iterate over each row
        for index, rows in full_prediction.iterrows():
            #fill nan
            rows = rows.fillna(0)
            # Create list for the current row
            my_list = rows.values.tolist()
            # print(my_list)
            
            my_list_per3 = [my_list[i:i+3] for i in range(0, len(my_list), 3)]
            # append the list to the final list
            Row_list_prediction.append(my_list_per3)

        # print(len(Row_list_prediction), len(Row_list_prediction[0]),len(Row_list_prediction[0][0]))
        plot(test_datapath + test_music_list[num_count] + ".mid", "./video_" + filecode + "_test_predict.mp4", Row_list_prediction[:800], None, 40, filecode) #ow_list[0:900]
        # print("prediction.shape", prediction.shape)
        prediction_arr = np.array(Row_list_prediction)
        # formated_motion = prediction_format(full_prediction)
        # # # plot(formated_motion)
        # audio_path = test_music_list[num_count][0]
        # output_path = "test_output_" + filecode + ".mp4"
        # plot(formated_motion, audio_path, output_path, None, 10, filecode)
        num_count += 1

# model.train()

test_input (1, 8172, 28)
prediction.shape (1, 8172, 102)
full_prediction (8172, 102)
81600
limit 800
[[[ 0.08871101  0.12147492  1.0978506 ]
  [ 0.01708137  0.08544757  1.11877952]
  [ 0.12872793  0.05573034  1.09563134]
  ...
  [ 0.03115049  0.09487166  0.98368618]
  [-0.13727589  0.04981044  1.09999708]
  [ 0.09120489  0.27696773  0.8203123 ]]

 [[ 0.0776111   0.10697879  1.08946655]
  [ 0.00891495  0.07362891  1.10603533]
  [ 0.1232987   0.04412632  1.09317384]
  ...
  [ 0.02993743  0.08544429  0.96475253]
  [-0.09693424  0.07375862  1.05980954]
  [ 0.09662688  0.22903611  0.76461635]]

 [[ 0.06177191  0.09969328  1.10029743]
  [-0.00264613  0.06360016  1.11539838]
  [ 0.10918397  0.03741877  1.10285256]
  ...
  [ 0.02163168  0.08136316  0.97369835]
  [-0.11765184  0.07203431  1.0877243 ]
  [ 0.09622837  0.21394673  0.76840988]]

 ...

 [[ 0.1022544   0.08463703  1.10410104]
  [ 0.0378343   0.0464834   1.11776242]
  [ 0.14795366  0.02204023  1.1003953 ]
  ...
  [ 0.05984664  0.07119

fluidsynth: panic: An error occurred while reading from stdin.


FluidSynth runtime version 2.1.1
Copyright (C) 2000-2020 Peter Hanappe and others.
Distributed under the LGPL license.
SoundFont(R) is a registered trademark of E-mu Systems, Inc.

Rendering audio to file './outputvs1-1ada.wav'..


ffmpeg version 4.2.2 Copyright (c) 2000-2019 the FFmpeg developers
  built with gcc 7.3.0 (crosstool-NG 1.23.0.449-a04d0)
  configuration: --prefix=/home/ilc/anaconda3/envs/sinica --cc=/tmp/build/80754af9/ffmpeg_1587154242452/_build_env/bin/x86_64-conda_cos6-linux-gnu-cc --disable-doc --enable-avresample --enable-gmp --enable-hardcoded-tables --enable-libfreetype --enable-libvpx --enable-pthreads --enable-libopus --enable-postproc --enable-pic --enable-pthreads --enable-shared --enable-static --enable-version3 --enable-zlib --enable-libmp3lame --disable-nonfree --enable-gpl --enable-gnutls --disable-openssl --enable-libopenh264 --enable-libx264
  libavutil      56. 31.100 / 56. 31.100
  libavcodec     58. 54.100 / 58. 54.100
  libavformat    58. 29.100 / 58. 29.100
  libavdevice    58.  8.100 / 58.  8.100
  libavfilter     7. 57.100 /  7. 57.100
  libavresample   4.  0.  0 /  4.  0.  0
  libswscale      5.  5.100 /  5.  5.100
  libswresample   3.  5.100 /  3.  5.100
  libpostproc    55

test_input (1, 6989, 28)
prediction.shape (1, 6989, 102)
full_prediction (6989, 102)
81600
limit 800
[[[ 0.07814759  0.1252442   1.0990207 ]
  [ 0.00632392  0.084382    1.11893508]
  [ 0.11866338  0.0577511   1.09766195]
  ...
  [ 0.0217576   0.09719401  0.98586277]
  [-0.14818716  0.06769846  1.11090097]
  [ 0.08427483  0.27140772  0.79224608]]

 [[ 0.05765808  0.12706885  1.09695563]
  [-0.00977285  0.09497971  1.11690435]
  [ 0.1001922   0.06629761  1.10802565]
  ...
  [ 0.00877394  0.09259284  0.98677204]
  [-0.16962503  0.03796935  1.08425448]
  [ 0.07485373  0.27200562  0.83153168]]

 [[ 0.05437301  0.1136651   1.10236762]
  [-0.00976541  0.07964701  1.11998115]
  [ 0.09792879  0.05341122  1.11140285]
  ...
  [ 0.0103806   0.08340127  0.98973796]
  [-0.16395982  0.03399078  1.0838894 ]
  [ 0.08346103  0.2627506   0.8289542 ]]

 ...

 [[ 0.08865882  0.10486563  1.10350761]
  [ 0.02299657  0.06192873  1.12015376]
  [ 0.13423738  0.04094802  1.09900967]
  ...
  [ 0.04302065  0.08327

...

ffmpeg version 4.2.2 Copyright (c) 2000-2019 the FFmpeg developers
  built with gcc 7.3.0 (crosstool-NG 1.23.0.449-a04d0)
  configuration: --prefix=/home/ilc/anaconda3/envs/sinica --cc=/tmp/build/80754af9/ffmpeg_1587154242452/_build_env/bin/x86_64-conda_cos6-linux-gnu-cc --disable-doc --enable-avresample --enable-gmp --enable-hardcoded-tables --enable-libfreetype --enable-libvpx --enable-pthreads --enable-libopus --enable-postproc --enable-pic --enable-pthreads --enable-shared --enable-static --enable-version3 --enable-zlib --enable-libmp3lame --disable-nonfree --enable-gpl --enable-gnutls --disable-openssl --enable-libopenh264 --enable-libx264
  libavutil      56. 31.100 / 56. 31.100
  libavcodec     58. 54.100 / 58. 54.100
  libavformat    58. 29.100 / 58. 29.100
  libavdevice    58.  8.100 / 58.  8.100
  libavfilter     7. 57.100 /  7. 57.100
  libavresample   4.  0.  0 /  4.  0.  0
  libswscale      5.  5.100 /  5.  5.100
  libswresample   3.  5.100 /  3.  5.100
  libpostproc    55

test_input (1, 7898, 28)
prediction.shape (1, 7898, 102)
full_prediction (7898, 102)
81600
limit 800
[[[ 7.81602859e-02  1.19434729e-01  1.09806756e+00]
  [ 1.14780553e-02  7.93808773e-02  1.11771820e+00]
  [ 1.21888675e-01  5.23642302e-02  1.09363971e+00]
  ...
  [ 2.21922584e-02  9.86964405e-02  9.78055990e-01]
  [-1.39759719e-01  8.76868963e-02  1.15491567e+00]
  [ 5.46801984e-02  2.21254960e-01  7.70222282e-01]]

 [[ 6.49192855e-02  9.13492143e-02  1.11046848e+00]
  [ 9.94142145e-04  4.98709381e-02  1.12187824e+00]
  [ 1.11889027e-01  2.83842832e-02  1.10849652e+00]
  ...
  [ 2.49862447e-02  8.35047588e-02  9.75542700e-01]
  [-1.18990563e-01  9.02013406e-02  1.13128815e+00]
  [ 9.06570479e-02  1.92384541e-01  7.63875341e-01]]

 [[ 6.49833456e-02  8.46618563e-02  1.10996089e+00]
  [ 1.63718127e-03  4.50790897e-02  1.12098548e+00]
  [ 1.09605312e-01  2.08965242e-02  1.10713062e+00]
  ...
  [ 2.71857046e-02  7.92440772e-02  9.74898612e-01]
  [-1.15332976e-01  8.89131874e-02  1.1105030

fluidsynth: panic: An error occurred while reading from stdin.


FluidSynth runtime version 2.1.1
Copyright (C) 2000-2020 Peter Hanappe and others.
Distributed under the LGPL license.
SoundFont(R) is a registered trademark of E-mu Systems, Inc.

Rendering audio to file './outputvs1-4prs.wav'..


ffmpeg version 4.2.2 Copyright (c) 2000-2019 the FFmpeg developers
  built with gcc 7.3.0 (crosstool-NG 1.23.0.449-a04d0)
  configuration: --prefix=/home/ilc/anaconda3/envs/sinica --cc=/tmp/build/80754af9/ffmpeg_1587154242452/_build_env/bin/x86_64-conda_cos6-linux-gnu-cc --disable-doc --enable-avresample --enable-gmp --enable-hardcoded-tables --enable-libfreetype --enable-libvpx --enable-pthreads --enable-libopus --enable-postproc --enable-pic --enable-pthreads --enable-shared --enable-static --enable-version3 --enable-zlib --enable-libmp3lame --disable-nonfree --enable-gpl --enable-gnutls --disable-openssl --enable-libopenh264 --enable-libx264
  libavutil      56. 31.100 / 56. 31.100
  libavcodec     58. 54.100 / 58. 54.100
  libavformat    58. 29.100 / 58. 29.100
  libavdevice    58.  8.100 / 58.  8.100
  libavfilter     7. 57.100 /  7. 57.100
  libavresample   4.  0.  0 /  4.  0.  0
  libswscale      5.  5.100 /  5.  5.100
  libswresample   3.  5.100 /  3.  5.100
  libpostproc    55

In [ ]:
model.eval()

full_prediction = pd.DataFrame()
num_count = 0
# read midi
# test_dataloader = get_dataloader(test_datapath, batch_size=1)
for test_batch in test_data_list:
    with torch.no_grad():
        first_target = torch.zeros(test_batch.shape[0],102)
        print(first_target.shape)
        test_input = test_batch[None, :]
        test_target = first_target[None, :]
        print("test_input", test_input.shape)
        print("test_target", test_target.shape)
        prediction = predict(model, test_input, device)
        
        # print(prediction.shape)
        
        prediction  = prediction[:, :, :102]
        print("prediction.shape", prediction.shape)
        
        # full_prediction.append(prediction)
        full_prediction = pd.DataFrame(prediction[0])
        print("full_prediction", full_prediction.shape)
        
        # prev_prediction = prediction[0][:-1][None, :]
        # print(prev_prediction.shape)
        
        Row_list_prediction =[]
        
        filecode = test_music_list[num_count]
    
        # Iterate over each row
        for index, rows in full_prediction.iterrows():
            #fill nan
            rows = rows.fillna(0)
            # Create list for the current row
            my_list = rows.values.tolist()
            # print(my_list)
            
            my_list_per3 = [my_list[i:i+3] for i in range(0, len(my_list), 3)]
            # append the list to the final list
            Row_list_prediction.append(my_list_per3)

        prediction_arr = np.array(Row_list_prediction)
        if not os.path.exists('./output_prediction/[audio_no_annotation]'+str(num_layers)+'LSTM_hidden'+str(hidden_size)+'_'+str(num_epochs)+'epoch/'):
            os.makedirs('./output_prediction/[audio_no_annotation]'+str(num_layers)+'LSTM_hidden'+str(hidden_size)+'_'+str(num_epochs)+'epoch/')
        midi_data_output = open('./output_prediction/[audio_no_annotation]'+str(num_layers)+'LSTM_hidden'+str(hidden_size)+'_'+str(num_epochs)+'epoch/prediction_'+
                                filecode +'.pkl', 'wb')
        pickle.dump(prediction_arr, midi_data_output)
        midi_data_output.close()
        
        num_count += 1

# model.train()

torch.Size([8172, 102])
test_input (1, 8172, 28)
test_target torch.Size([1, 8172, 102])
prediction.shape (1, 8172, 102)
full_prediction (8172, 102)
torch.Size([6989, 102])
test_input (1, 6989, 28)
test_target torch.Size([1, 6989, 102])
prediction.shape (1, 6989, 102)
full_prediction (6989, 102)
torch.Size([11534, 102])
test_input (1, 11534, 28)
test_target torch.Size([1, 11534, 102])
prediction.shape (1, 11534, 102)
full_prediction (11534, 102)
torch.Size([7898, 102])
test_input (1, 7898, 28)
test_target torch.Size([1, 7898, 102])
prediction.shape (1, 7898, 102)
full_prediction (7898, 102)


In [ ]:
final_val_loss = evaluate_lstm(model, val_dataloader)

Validation
len(audio_data) 6706
len(motion_data) 6706
len(audio_data) 5281
len(motion_data) 5281
len(audio_data) 4525
len(motion_data) 4525
len(audio_data) 6061
len(motion_data) 6061
len(audio_data) 6069
len(motion_data) 6069
inputs.shape: torch.Size([5, 6706, 28])
targets.shape: torch.Size([5, 6706, 102])
outputs.shape: torch.Size([5, 6706, 102])


In [ ]:
print(final_val_loss)

0.0021074414253234863


In [ ]:
final_l1_loss = evaluate_l1(model, val_dataloader)
print(final_l1_loss)

Validation L1
len(audio_data) 6706
len(motion_data) 6706
len(audio_data) 6069
len(motion_data) 6069
len(audio_data) 6061
len(motion_data) 6061
len(audio_data) 4525
len(motion_data) 4525
len(audio_data) 5281
len(motion_data) 5281
inputs.shape: torch.Size([5, 6706, 28])
targets.shape: torch.Size([5, 6706, 102])
outputs.shape: torch.Size([5, 6706, 102])
0.028452297672629356
